In [74]:
--Cleaning data on alternative fuel stations using queries in SQL Server 
--Data from https://afdc.energy.gov/data_download

--Initial query to take a look at the data
SELECT * FROM dbo.alt_fuel_stations
ORDER BY ID
OFFSET 0 ROWS FETCH FIRST 10 ROWS ONLY;

(10 rows affected)

Total execution time: 00:00:00.020

Fuel_Type_Code Station_Name Street_Address City State ZIP Status_Code Expected_Date Groups_With_Access_Code NG_Fill_Type_Code EV_Other_Info EV_Network Geocode_Status Latitude Longitude Date_Last_Confirmed ID Updated_At Owner_Type_Code Open_Date NG_Vehicle_Class Country Intersection_Directions_French Access_Days_Time_French BD_Blends_French Groups_With_Access_Code_French Hydrogen_Is_Retail Access_Code Access_Detail_Code Federal_Agency_Code Facility_Type CNG_Dispenser_Num CNG_On_Site_Renewable_Source CNG_Total_Compression_Capacity CNG_Storage_Capacity LNG_On_Site_Renewable_Source E85_Other_Ethanol_Blends EV_Pricing EV_Pricing_French LPG_Nozzle_Types Hydrogen_Pressures Hydrogen_Standards CNG_Fill_Type_Code CNG_PSI CNG_Vehicle_Class LNG_Vehicle_Class EV_On_Site_Renewable_Source Restricted_Access RD_Blends RD_Blends_French RD_Blended_with_Biodiesel RD_Maximum_Biodiesel_Level NPS_Unit_Name CNG_Station_Sells_Renewable_Natural_Gas LNG_Station_Sells_Renewable_Natural_Gas CNG Spire - Montgomery Operations Center 2951 Chestnut St Montgomery AL 36107 E NULL Private B NULL NULL 200-9 32.367916 -86.267021 2023-04-06 17 2023-04-06 17:17:01 UTC T 2010-12-01 MD US NULL NULL NULL Privé NULL private NULL NULL STANDALONE_STATION NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL B 3600 MD NULL NULL NULL NULL NULL NULL NULL NULL 0 NULL CNG Metropolitan Atlanta Rapid Transit Authority 2424 Piedmont Rd NE Atlanta GA 30324 E NULL Private - Government only Q NULL NULL 200-8 33.821911 -84.367461 2023-01-10 45 2023-02-14 15:54:11 UTC LG 1996-12-15 LD US NULL NULL NULL Privé - Réservé au gouvernement NULL private GOVERNMENT NULL FLEET_GARAGE NULL NULL 30 NULL NULL NULL NULL NULL NULL NULL NULL Q 3000 LD NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL CNG United Parcel Service 270 Marvin Miller Dr Atlanta GA 30336 E NULL Private B NULL NULL 200-9 33.760256 -84.543822 2022-06-14 64 2023-02-14 15:54:11 UTC P 1997-01-01 HD US NULL NULL NULL Privé NULL private NULL NULL STANDALONE_STATION NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL B 3600 HD NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL CNG Arkansas Oklahoma Gas Corp 2100 S Waldron Rd Fort Smith AR 72903 E NULL Public - Credit card at all times Q NULL NULL 200-9 35.362213 -94.375338 2023-02-13 73 2023-02-14 15:54:11 UTC T 1997-01-01 MD US NULL NULL NULL Public - Carte de crédit en tout temps NULL public CREDIT_CARD_ALWAYS NULL UTILITY 1 NULL 250 57855 NULL NULL NULL NULL NULL NULL NULL Q 3600 MD NULL NULL 0 NULL NULL NULL NULL NULL 0 NULL CNG Clean Energy - Logan International Airport 1000 Cottage St Ext East Boston MA 02128 E NULL Public - Credit card at all times Q NULL NULL GPS 42.37470554648246 -71.02654860574343 2022-12-13 81 2023-02-14 15:54:11 UTC SG 1996-11-15 MD US NULL NULL NULL Public - Carte de crédit en tout temps NULL public CREDIT_CARD_ALWAYS NULL AIRPORT 4 NONE 850 NULL NULL NULL NULL NULL NULL NULL NULL Q 3000 3600 MD NULL NULL 0 NULL NULL NULL NULL NULL 1 NULL CNG Clean Energy - Everett - National Grid 16 Rover St Everett MA 02149 E NULL Public - Credit card at all times Q NULL NULL 200-8 42.393167 -71.064352 2022-12-13 84 2023-02-14 15:54:11 UTC T 1996-11-15 HD US NULL NULL NULL Public - Carte de crédit en tout temps NULL public CREDIT_CARD_ALWAYS NULL STANDALONE_STATION 1 NULL 425 NULL NULL NULL NULL NULL NULL NULL NULL Q 3000 3600 HD NULL NULL 0 NULL NULL NULL NULL NULL 0 NULL CNG Clean Energy - Greenpoint - National Grid 287 Maspeth Ave Brooklyn NY 11211 E NULL Public - Credit card at all times Q NULL NULL 200-8 40.718037 -73.932309 2022-12-13 108 2023-02-14 15:54:11 UTC T 2016-07-15 HD US NULL NULL NULL Public - Carte de crédit en tout temps NULL public CREDIT_CARD_ALWAYS NULL UTILITY 1 NULL 1200 NULL NULL NULL NULL NULL NULL NULL NULL Q 3000 3600 HD NULL NULL 0 NULL NULL NULL NULL NULL 0 NULL CNG Canarsie - National Grid 8424 Ditmas Ave Brooklyn NY 11236 E NULL Public - Credit card at all times B NULL NULL 200-8 40.64554 -73.918344 2022-12-13 112 2023-02-14 15:54:1

In [18]:
--Checking for null values in State, ZIP, and Country fields since I am interested in the geographic distribution of fueling stations
SELECT State, ZIP, Country from dbo.alt_fuel_stations
    WHERE State is null or ZIP is null or Country is null


(31 rows affected)

Total execution time: 00:00:00.057

State ZIP Country NULL 90808 US NULL 85015 US NULL 85395 US NULL 32817 US NULL 90403 US NULL 97225 US NULL 95343 US NULL 60093 US NULL 78758 US NULL 75035 US NULL 29585 US NULL 46227 US NULL 43023 US NULL 95126 US NULL 85258 US NULL 80301 US NULL 75033 US NULL 85004 US NULL 28211 US NULL 85331 US NULL 98901 US NULL 76018 US NULL 18017 US NULL 32550 US NULL 65807 US NULL 33954 US NULL 44146 US NULL 85750 US NULL 52136 US NULL 33149 US NULL 7601 US

In [65]:
--Looks there are no null country or zip code values, but there are null states. 
--However, I can fill the missing state values in from the zip codes using a table imported from https://simplemaps.com/data/us-zips

UPDATE dbo.alt_fuel_stations
SET State = COALESCE(State, (SELECT state_name FROM dbo.uszips WHERE dbo.uszips.zip = dbo.alt_fuel_stations.ZIP))

--Checking that it worked
SELECT State, ZIP, Country from dbo.alt_fuel_stations
    WHERE State is null or ZIP is null or Country is null

--Looks like there is only one ZIP code where the corresponding state couldn't be found!

(71188 rows affected)

(1 row affected)

Total execution time: 00:00:00.208

State ZIP Country NULL 95343 US

In [66]:
--Make a new table containing only the desired columns about station's type, location, and access using DISTINCT to not include duplicates
DROP Table if exists dbo.alt_fuel_stations_clean
SELECT DISTINCT ID, Fuel_type_code, Station_Name, City, State, ZIP, Country, Status_Code, Access_Code, Facility_Type 
    INTO dbo.alt_fuel_stations_clean FROM dbo.alt_fuel_stations
    WHERE City is not NULL and State is not NULL and Country is not NULL and Status_Code is not NULL and Access_Code is not NULL


(71186 rows affected)

Total execution time: 00:00:00.123

In [67]:
--Replace null Facility_Type values with "unknown"
UPDATE dbo.alt_fuel_stations_clean
SET Facility_Type = COALESCE(Facility_Type,'unknown')

(71186 rows affected)

Total execution time: 00:00:00.391

In [68]:
--Make new column with the full name of the status based on the code
ALTER TABLE dbo.alt_fuel_stations_clean
ADD Status NVARCHAR(255);

Commands completed successfully.

Total execution time: 00:00:00.016

In [69]:
--Replace status codes with written out descriptions for increased readability
UPDATE dbo.alt_fuel_stations_clean
SET Status = 
    CASE  WHEN Status_Code = 'E' THEN 'Available'
          WHEN Status_Code = 'P' THEN 'Planned'
          ELSE 'Temporarily Unavailable'
          END

(71186 rows affected)

Total execution time: 00:00:00.542

In [70]:
--Make new column with the full name of the fuel type
ALTER TABLE dbo.alt_fuel_stations_clean
ADD Fuel_Type NVARCHAR(255);

Commands completed successfully.

Total execution time: 00:00:00.011

In [71]:
--Fill new column with the fuel type description from the dataset documentation
UPDATE dbo.alt_fuel_stations_clean
SET Fuel_type = CASE WHEN Fuel_type_code = 'BD' THEN 'Biodiesel (B20 and above)'
    WHEN Fuel_type_code = 'CNG' THEN 'Compressed Natural Gas'
    WHEN Fuel_type_code = 'ELEC' THEN 'Electric'
    WHEN Fuel_type_code = 'E85' THEN 'Ethanol (E85)'
    WHEN Fuel_type_code = 'HY' THEN 'Hydrogen'
    WHEN Fuel_type_code = 'LNG' THEN 'Liquefied Natural Gas'
    WHEN Fuel_type_code = 'LPG' THEN 'Propane (LPG)'
    WHEN Fuel_type_code = 'RD' THEN 'Renewable Diesel (R20 and above)'
    END

(71186 rows affected)

Total execution time: 00:00:00.571

In [72]:
--Trimming trailing spaces and removing underscores from Facility type, and making lowercase
UPDATE dbo.alt_fuel_stations_clean
SET Facility_Type = REPLACE(LOWER(TRIM(Facility_Type)), '_', ' ')

(71186 rows affected)

Total execution time: 00:00:00.185

In [73]:
--Check to make sure the data look good
SELECT * FROM dbo.alt_fuel_stations_clean

(71186 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:00.607

ID Fuel_type_code Station_Name City State ZIP Country Status_Code Access_Code Facility_Type Status Fuel_Type 17 CNG Spire - Montgomery Operations Center Montgomery AL 36107 US E private standalone station Available Compressed Natural Gas 45 CNG Metropolitan Atlanta Rapid Transit Authority Atlanta GA 30324 US E private fleet garage Available Compressed Natural Gas 64 CNG United Parcel Service Atlanta GA 30336 US E private standalone station Available Compressed Natural Gas 73 CNG Arkansas Oklahoma Gas Corp Fort Smith AR 72903 US E public utility Available Compressed Natural Gas 81 CNG Clean Energy - Logan International Airport East Boston MA 02128 US E public airport Available Compressed Natural Gas 84 CNG Clean Energy - Everett - National Grid Everett MA 02149 US E public standalone station Available Compressed Natural Gas 108 CNG Clean Energy - Greenpoint - National Grid Brooklyn NY 11211 US E public utility Available Compressed Natural Gas 112 CNG Canarsie - National Grid Brooklyn NY 11236 US E public utility Available Compressed Natural Gas 124 CNG Con Edison - W 29th St Service Center New York NY 10001 US E public utility Available Compressed Natural Gas 125 CNG Con Edison - E 16th St Service Center New York NY 10009 US E public utility Available Compressed Natural Gas 129 CNG Con Edison - Van Nest Service Center Bronx NY 10462 US E public utility Available Compressed Natural Gas 130 CNG Con Edison - Rye Service Center Rye NY 10580 US E public utility Available Compressed Natural Gas 132 CNG Con Edison - College Point Service Center Queens NY 11354 US E public utility Available Compressed Natural Gas 147 CNG CNG Source Fueling - Greene's Auto & Truck Service Indianapolis IN 46225 US E public standalone station Available Compressed Natural Gas 215 CNG Black Hills Energy Cheyenne WY 82001 US E public utility Available Compressed Natural Gas 248 CNG Shell Hartford CT 06114 US T public convenience store Temporarily Unavailable Compressed Natural Gas 296 CNG Sparq - Baton Rouge Baton Rouge LA 70815 US E public standalone station Available Compressed Natural Gas 360 CNG Clean Energy - City of Santa Fe - Santa Fe Trails Transit Santa Fe NM 87507 US E public fleet garage Available Compressed Natural Gas 372 CNG Kansas Gas Service Overland Park KS 66214 US E public utility Available Compressed Natural Gas 408 CNG Intermountain Gas Co Boise ID 83709 US E private utility Available Compressed Natural Gas 413 CNG Intermountain Gas Co Pocatello ID 83202 US E private utility Available Compressed Natural Gas 415 CNG Intermountain Gas Co Idaho Falls ID 83401 US E private utility Available Compressed Natural Gas 416 CNG Intermountain Gas Co Nampa ID 83651 US E private utility Available Compressed Natural Gas 418 CNG ValleyRide Boise ID 83705 US E private fleet garage Available Compressed Natural Gas 434 CNG Kansas Gas Service Topeka KS 66603 US E public utility Available Compressed Natural Gas 448 CNG Clean Energy - Brentwood - National Grid Brentwood NY 11717 US T public utility Temporarily Unavailable Compressed Natural Gas 453 CNG Clean Energy - City of Irving Irving TX 75061 US E public muni gov Available Compressed Natural Gas 456 CNG Clean Energy - Downtown Dallas Dallas TX 75207 US E public gas station Available Compressed Natural Gas 477 CNG Clean Energy - Garland Independent School District Garland TX 75042 US E public school Available Compressed Natural Gas 523 CNG Jordan School District West Jordan UT 84088 US E private school Available Compressed Natural Gas 528 CNG Questar Gas - Salt Lake City Salt Lake City UT 84104 US E public standalone station Available Compressed Natural Gas 548 CNG Questar Gas - LW's Conoco Logan UT 84321 US E public convenience store Available Compressed Natural Gas 558 CNG Dominion Energy - Market Express Sinclair Price UT 84501 US E public convenience store Available Compressed Natural Gas 569 CNG Questar Gas - Chevron Richfield UT 84701 US E public gas station Available Compressed Natural Gas 597 CNG 